For cuML see the installation guide [here](https://docs.rapids.ai/install/)

In [1]:
%pip install --extra-index-url=https://pypi.nvidia.com "cuml-cu12==25.8.*"
%pip install --upgrade kaleido

Looking in indexes: https://pypi.org/simple, https://pypi.nvidia.com
Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.


### Импорты и загрузка данных

In [2]:
# Меняем путь на уровень ниже, чтобы делать импорты из модулей
import os
os.chdir(os.path.dirname(os.getcwd()))

In [3]:
from warnings import simplefilter
simplefilter("ignore", Warning)

import polars as pl
import cudf
from cuml.metrics import roc_auc_score
from cuml.explainer import KernelExplainer
from cuml.ensemble import RandomForestClassifier
from sklearn.metrics import classification_report
from sklearn.metrics import precision_recall_curve, average_precision_score

from feature_engineering import balance_data, prepare_for_training
from visualization import plot_confusion_matrix, plot_pr_auc, plot_roc_auc, plot_shap

In [4]:
features = pl.read_parquet("data/features.parquet", low_memory=True)

### Балансировка и подготовка к обучению (сэмплинг)

In [5]:
balanced_df = balance_data(features)
gdf = cudf.from_pandas(balanced_df)
X_train, X_test, y_train, y_test = prepare_for_training(gdf)

### Обучение базовой модели

In [6]:
model = RandomForestClassifier(
    n_estimators=100,
    max_depth=7,
    random_state=42,
    criterion='gini',
    n_bins=256,       # Оптимально для производительности
    bootstrap=True,   # Бэггинг
    max_features=0.3, # Оптимально для обнаружения мошенничества
    max_samples=0.8   # Субдискретизация для балансировки классов
)
model.fit(X_train, y_train)

RandomForestClassifier()

### Оцениваем модель

In [7]:
y_pred = model.predict(X_test)
y_proba = model.predict_proba(X_test)

In [8]:
print(classification_report(y_test.to_numpy(), y_pred.to_numpy()))

              precision    recall  f1-score   support

           0       0.95      0.94      0.94    168734
           1       0.94      0.95      0.94    168734

    accuracy                           0.94    337468
   macro avg       0.94      0.94      0.94    337468
weighted avg       0.94      0.94      0.94    337468



In [9]:
roc_auc = roc_auc_score(y_test, y_proba[1])
y_proba = model.predict_proba(X_test)
precision, recall, thresholds = precision_recall_curve(y_test.to_numpy(), y_proba[1].to_numpy())
ap = average_precision_score(y_test.to_numpy(), y_proba[1].to_numpy())

print("AUC Score:", roc_auc)
print("PR AUC:", ap)

AUC Score: 0.9879876375198364
PR AUC: 0.9882819779141527


### Визуальзация результатов

#### Матрица ошибок, ROC-AUC и PR-AUC кривые

In [10]:
y_scores = y_proba[1].to_numpy().ravel()
y_true = y_test.to_numpy().astype(int)

In [11]:
# Рассчет матрицы ошибок
plot_confusion_matrix(y_test, y_pred).show()

Здесь мы подбираем J-индекс (индекс Юдена), который минимизирует разницу между истинно положительными и ложно положительными результатами.

In [12]:
plot_roc_auc(y_true, y_scores)

In [13]:
plot_pr_auc(y_true, y_scores)

#### SHAP-интерпретация

In [14]:
# Подготовка данных
background_data = X_train.sample(n=500, random_state=42)  # Используем подвыборку

# Инициализация и расчет SHAP значений
kexplainer = KernelExplainer(
    model=model.predict_proba,  # Используем вероятности
    data=background_data,
    nsamples=1000,  # Оптимально для баланса скорость/точность
    is_gpu_model=True,
    random_state=42
)

# Расчет для тестовой выборки (первые 500 образцов)
test_sample = X_test[:500]
shap_values_kernel = kexplainer.shap_values(test_sample)

In [15]:
# shap_values_kernel[1] содержит значения для класса 1 (мошенничество)
shap_matrix = shap_values_kernel[1]  # shape=(100, 59)
# Получение имен признаков
feature_names = X_test.columns.tolist()
plot_shap(shap_matrix, feature_names)